In [64]:
import json
import requests
from misc import nearest_mrt
import pickle
import os
import pandas as pd
import datetime
from datetime import datetime

In [5]:
filename = 'finalized_model2.sav'

if os.path.exists("./finalized_model2.sav"):
    model = pickle.load(open(filename, 'rb'))
    print('loaded model')
else:
    print('failed loading model')

loaded model


In [8]:
model

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(transformers=[('standardscaler',
                                                  StandardScaler(),
                                                  ['distance_mrt',
                                                   'age_transation',
                                                   'transaction_yr', 'Postal',
                                                   'storey_height']),
                                                 ('pipeline',
                                                  Pipeline(steps=[('onehotencoder',
                                                                   OneHotEncoder(handle_unknown='ignore',
                                                                                 sparse_output=False))]),
                                                  ['town', 'flat_num'])])),
                ('xgbregressor',
                 XGBRegressor(base_scor...
                              feature_types=None, gamma=1, grow_policy=None,
                              importance_type=None,
                              interaction_constraints=None, learning_rate=None,
                              max_bin=None, max_cat_threshold=None,
                              max_cat_to_onehot=None, max_delta_step=None,
                              max_depth=7, max_leaves=None,
                              min_child_weight=None, missing=nan,
                              monotone_constraints=None, multi_strategy=None,
                              n_estimators=None, n_jobs=None,
                              num_parallel_tree=None, random_state=None, ...))])

In [20]:
#extract feature names#
feature_names = model.feature_names_in_.tolist()
input = [0]*len(feature_names)

In [21]:
feature_names

['distance_mrt',
 'age_transation',
 'transaction_yr',
 'Postal',
 'storey_height',
 'town',
 'flat_num']

In [22]:
#Set up mrt_list
mrt_name = []
mrt_loc = []
with open('data/mrt_list.json', 'r') as file:
    for line in file:
        item = json.loads(line)
        mrt_name.append(item['MRT'])
        loc = tuple([float(i) for i in item['location']])
        mrt_loc.append(loc)

In [23]:
#Test input
Postal_,age_,town_,storey_,room_ = 680705, 30, 'CHOA CHU KANG', 12, '5 ROOM'

In [24]:
##POSTAL
Postal_input = int(Postal_)
# Postal_input = 680705
input[feature_names.index('Postal')] = Postal_input

In [45]:
##DISTANCE TO MRT
search_term = Postal_
query_string= 'https://www.onemap.gov.sg/api/common/elastic/search?searchVal={}&returnGeom=Y&getAddrDetails=Y&pageNum=1'.format(search_term)
resp = requests.get(query_string)
data = json.loads(resp.content)
print(query_string)
print(data)
chosen_result = data['results'][0]

#Calculate the distance to nearest MRT
distance_km, nearest_mr = nearest_mrt(chosen_result['LATITUDE'], chosen_result['LONGITUDE'], mrt_name, mrt_loc)
input[feature_names.index('distance_mrt')] = distance_km
nearest_mr

https://www.onemap.gov.sg/api/common/elastic/search?searchVal=680705&returnGeom=Y&getAddrDetails=Y&pageNum=1
{'found': 1, 'totalNumPages': 1, 'pageNum': 1, 'results': [{'SEARCHVAL': '705 CHOA CHU KANG STREET 53 SINGAPORE 680705', 'BLK_NO': '705', 'ROAD_NAME': 'CHOA CHU KANG STREET 53', 'BUILDING': 'NIL', 'ADDRESS': '705 CHOA CHU KANG STREET 53 SINGAPORE 680705', 'POSTAL': '680705', 'X': '18296.4178872742', 'Y': '41364.999289671', 'LATITUDE': '1.39036325274643', 'LONGITUDE': '103.746124351793'}]}


'Choa Chu Kang MRT Station'

In [62]:
##STOREY
#Height is input, but then converted to the scale we used for iterating model
height_input = int(storey_)
# height_input = 51
Height = (height_input+2)//3
input[feature_names.index('storey_height')] = Height

##Town
input[feature_names.index("town")]=town_

##Room
input[feature_names.index("flat_num")]=room_

##AGE/ TRANSACTION YEAR [Current default to 2024]
age_input = int(age_)
# age_input = 30

# Get the current date
current_date = datetime.now()

input[feature_names.index('age_transation')] = age_input
input[feature_names.index('transaction_yr')] = current_date.year  #Default to 2024 first

input

[0.5863143456991471, 30, 2024, 680705, 4, 'CHOA CHU KANG', '5 ROOM']

In [69]:
#Create final_dataframe as input to model

Actual = dict(zip(feature_names,input))
Actual_df = pd.DataFrame(Actual, index=[0])
resale_adj_price = model.predict(Actual_df)[0]
resale_adj_price

468224.38

In [70]:
# Calculate the quarter
quarter = (current_date.month - 1) // 3 + 1
# Format the quarter in the desired format
formatted_quarter = f"{quarter}Q{current_date.year}"

In [71]:
formatted_quarter

'1Q2024'

In [74]:
RPI_pd = pd.read_csv('data/RPI_dict.csv', header=None)
RPI_dict = dict(zip(RPI_pd[0], RPI_pd[1]))
RPI = float(RPI_dict[formatted_quarter])
price = resale_adj_price*(RPI/133.9) 
price

636421.4805825242

## Find last 10 as dataframe

In [106]:
df = pd.read_json("data/data_features.json", lines=True)

Postal_input= 680705
df_filtered = df[df['Postal']==str(Postal_input)]

df_output=df_filtered.sort_values(by='transaction_yr', ascending=False).head(10).reset_index(drop=True)

storey_dict = {
    '01 TO 03': 1, '04 TO 06': 2, '07 TO 09': 3, '10 TO 12': 4,
    '13 TO 15': 5, '16 TO 18': 6, '19 TO 21': 7, '22 TO 24': 8,
    '25 TO 27': 9, '28 TO 30': 10, '31 TO 33': 11, '34 TO 36': 12,
    '37 TO 39': 13, '40 TO 42': 14, '43 TO 45': 15, '46 TO 48': 16,
    '49 TO 51': 17
}

# Swap keys and values using dictionary comprehension
swapped_dict = {value: key for key, value in storey_dict.items()}

df_output['storey_height']=df_output['storey_height'].apply(lambda x: swapped_dict[x])
df_out = df_output[['transaction','area','storey_height','resale_price']]

df_out

transaction   area storey_height  resale_price
0     2023-04  114.0      07 TO 09        510000
1     2022-06  132.0      10 TO 12        585000
2     2022-12  109.0      01 TO 03        470000
3     2021-03  121.0      07 TO 09        455000
4     2020-02  109.0      07 TO 09        329000
5     2019-05  114.0      04 TO 06        330000
6     2017-09  109.0      10 TO 12        355000